In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

In [0]:
# Define the path to the Delta table in the bronze layer
bronze_table_path = "amazon.streamdb.streaming_raw"

# Read the streaming data from the Delta table
streaming_bronze_df = spark.readStream \
    .table(bronze_table_path)

In [0]:
from pyspark.sql.functions import from_json, col, get_json_object

# Extract the cart_contents JSON string from _rescued_data
parsed_df = streaming_bronze_df.withColumn("cart_contents_str", get_json_object(col("_rescued_data"), "$.cart_contents"))

In [0]:
# Define the schema for the cart_contents field
cart_contents_schema = "array<struct<product_id: string, quantity: int, price: double>>"

# Parse the cart_contents field from the JSON string
parsed_df = parsed_df.withColumn("cart_contents", from_json(col("cart_contents_str"), cart_contents_schema))

In [0]:
# Explode the cart_contents column to get individual product items
exploded_df = parsed_df.withColumn("exploded_cart_contents", explode_outer(col("cart_contents")))

# Create new columns based on the exploded data
exploded_df = exploded_df.withColumn("product_id_cart_contents", col("exploded_cart_contents.product_id")) \
    .withColumn("price_cart_contents", col("exploded_cart_contents.price")) \
    .withColumn("quantity_cart_contents", col("exploded_cart_contents.quantity"))


In [0]:
# Fill product_id and price using either the original values or the values from exploded cart_contents
cleaned_df = exploded_df.withColumn(
    "product_id",
    when(col("product_id").isNull(), col("product_id_cart_contents")).otherwise(col("product_id"))
).withColumn(
    "price",
    when(col("price").isNull(), col("price_cart_contents")).otherwise(col("price"))
).withColumn(
    "category",
    when(col("category").isNull() & col("filter_details").isNotNull(), split(col("filter_details"), ": ").getItem(1))
    .otherwise(col("category"))
)

# Drop the exploded_cart_contents column as it's no longer needed
cleaned_df = cleaned_df.drop("exploded_cart_contents")


In [0]:
# Ensure that null values are preserved where necessary, and all columns are displayed
final_df = cleaned_df.select(
    "timestamp",
    "user_id",
    "event_type",
    "device_type",
    "session_id",
    "EventProcessedUtcTime",
    "PartitionId",
    "EventEnqueuedUtcTime",
    "product_id",  # this is the combined product_id
    "category",  # combined category with filter_details
    "sub_category",
    "price",  # combined price with cart_contents
    "search_term",
    "product_id_cart_contents",
    "quantity_cart_contents",
    "price_cart_contents"
)

# Display the cleaned DataFrame
final_df.display()


timestamp user_id event_type device_type session_id EventProcessedUtcTime PartitionId EventEnqueuedUtcTime product_id category sub_category price search_term product_id_cart_contents quantity_cart_contents price_cart_contents 1.7234295201133268E9 CUST-14631 Add to Cart Mobile S959-4745249960 2024-08-12T02:25:20.763695Z 0 2024-08-12T02:25:20.639Z WW-561417 Women'S Clothing western wear null null null null null 1.7234295209070451E9 CUST-17226 Browse Product Desktop S647-5737266877 2024-08-12T02:25:21.561912Z 0 2024-08-12T02:25:21.514Z F-221971 home & kitchen Furniture null null null null null 1.7234295209729657E9 CUST-13727 Search Desktop S806-7767844990 2024-08-12T02:25:21.562041Z 0 2024-08-12T02:25:21.529Z null Accessories null null handbags & clutches null null null 1.7234295221478453E9 CUST-11875 Apply Filter Mobile S128-5985264117 2024-08-12T02:25:22.873224Z 0 2024-08-12T02:25:22.67Z null accessories null null null null null null 1.7234295240960817E9 CUST-08853 Browse Product Desktop S594-7571885355 2024-08-12T02:25:25.07663Z 0 2024-08-12T02:25:24.904Z CS-117376 men's shoes Casual Shoes null null null null null 1.7234295245287743E9 CUST-17226 Add to Cart Desktop S647-5737266877 2024-08-12T02:25:25.5142Z 0 2024-08-12T02:25:25.31Z F-221971 Home & Kitchen furniture null null null null null 1.7234295248170295E9 CUST-16063 AppLogin Mobile S485-7090286144 2024-08-12T02:25:25.51439Z 0 2024-08-12T02:25:25.389Z null null null null null null null null 1.7234295245831337E9 CUST-13727 Browse Product Desktop S806-7767844990 2024-08-12T02:25:25.514655Z 0 2024-08-12T02:25:25.404Z PCA-426149 beauty & health Personal Care Appliances null null null null null 1.7234295256875393E9 CUST-11875 Apply Filter Mobile S128-5985264117 2024-08-12T02:25:26.404585Z 0 2024-08-12T02:25:26.232Z null accessories null null null null null null 1.7234295293363063E9 CUST-17226 Browse Product Desktop S647-5737266877 2024-08-12T02:25:30.014005Z 0 2024-08-12T02:25:29.842Z J-335697 men's clothing Jeans null null null null null 1.723429529922018E9 CUST-08853 Search Desktop S594-7571885355 2024-08-12T02:25:30.780263Z 0 2024-08-12T02:25:30.654Z null Women'S Clothing null null ethnic wear null null null 1.723429530246815E9 CUST-11875 Search Mobile S128-5985264117 2024-08-12T02:25:31.107853Z 0 2024-08-12T02:25:30.92Z null Appliances null null all appliances null null null 1.7234295304006813E9 CUST-16063 Browse Product Mobile S485-7090286144 2024-08-12T02:25:31.108233Z 0 2024-08-12T02:25:31.029Z WW-575375 women's clothing Western Wear null null null null null 1.723429530499204E9 CUST-13727 Browse Product Desktop S806-7767844990 2024-08-12T02:25:31.108347Z 0 2024-08-12T02:25:31.045Z MF-415214 stores Men's Fashion null null null null null 1.7234295336797323E9 CUST-08853 Search Desktop S594-7571885355 2024-08-12T02:25:34.639063Z 0 2024-08-12T02:25:34.483Z null Women'S Clothing null null western wear null null null 1.7234295339805431E9 CUST-15987 Browse Product Desktop S352-3276363757 2024-08-12T02:25:34.857744Z 0 2024-08-12T02:25:34.67Z AE-046994 tv, audio & cameras All Electronics null null null null null 1.7234295341288753E9 CUST-07528 Apply Filter Desktop S308-9517299393 2024-08-12T02:25:34.857929Z 0 2024-08-12T02:25:34.67Z null accessories null null null null null null 1.7234295350993273E9 CUST-11078 Apply Filter Desktop S526-7423099512 2024-08-12T02:25:35.842016Z 0 2024-08-12T02:25:35.608Z null home & kitchen null null null null null null 1.7234295359345906E9 CUST-11875 Search Mobile S128-5985264117 2024-08-12T02:25:36.607621Z 0 2024-08-12T02:25:36.451Z null Tv, Audio & Cameras null null speakers null null null 1.723429537685823E9 CUST-15987 Add to Cart Desktop S352-3276363757 2024-08-12T02:25:38.373376Z 0 2024-08-12T02:25:38.233Z AE-046994 Tv, Audio & Cameras all electronics null null null null null 1.7234295377236638E9 CUST-07528 Browse Product Desktop S308-9517299393 2024-08-12T02:25:38.373563Z 0 2024-08-12T02:25:38.248Z R-430386 bags & luggage Rucksacks null null nu

In [0]:
%sql
drop table amazon.streamdb.streaming_cleaned;

In [0]:
%sql
CREATE TABLE amazon.streamdb.streaming_cleaned (
    timestamp DOUBLE,
    user_id STRING NOT NULL,
    event_type STRING,
    device_type STRING,
    session_id STRING NOT NULL,
    EventProcessedUtcTime TIMESTAMP,
    PartitionId LONG,
    EventEnqueuedUtcTime TIMESTAMP,
    product_id STRING,
    category STRING,
    sub_category STRING,
    price DOUBLE,
    search_term STRING,
    product_id_cart_contents STRING,
    quantity_cart_contents INT,
    price_cart_contents DOUBLE,
    PRIMARY KEY (EventProcessedUtcTime)
)
USING DELTA;


In [0]:
# checkpoint_path_window = "/mnt/amazonopcheckpoint/chekpointlocwindow"
checkpoint_path_silver = "/mnt/amazonopcheckpoint/chekpointlocsilver"

In [0]:
# Write the entire valid streaming data to the silver layer without specific columns
final_df.writeStream \
    .outputMode("append")\
    .option("checkpointLocation", checkpoint_path_silver ) \
    .toTable("amazon.streamdb.streaming_cleaned")

In [0]:
%sql
select * from amazon.streamdb.streaming_cleaned;

timestamp user_id event_type device_type session_id EventProcessedUtcTime PartitionId EventEnqueuedUtcTime product_id category sub_category price search_term product_id_cart_contents quantity_cart_contents price_cart_contents 1.7234295201133268E9 CUST-14631 Add to Cart Mobile S959-4745249960 2024-08-12T02:25:20.763695Z 0 2024-08-12T02:25:20.639Z WW-561417 Women'S Clothing western wear null null null null null 1.7234295209070451E9 CUST-17226 Browse Product Desktop S647-5737266877 2024-08-12T02:25:21.561912Z 0 2024-08-12T02:25:21.514Z F-221971 home & kitchen Furniture null null null null null 1.7234295209729657E9 CUST-13727 Search Desktop S806-7767844990 2024-08-12T02:25:21.562041Z 0 2024-08-12T02:25:21.529Z null Accessories null null handbags & clutches null null null 1.7234295221478453E9 CUST-11875 Apply Filter Mobile S128-5985264117 2024-08-12T02:25:22.873224Z 0 2024-08-12T02:25:22.67Z null accessories null null null null null null 1.7234295240960817E9 CUST-08853 Browse Product Desktop S594-7571885355 2024-08-12T02:25:25.07663Z 0 2024-08-12T02:25:24.904Z CS-117376 men's shoes Casual Shoes null null null null null 1.7234295245287743E9 CUST-17226 Add to Cart Desktop S647-5737266877 2024-08-12T02:25:25.5142Z 0 2024-08-12T02:25:25.31Z F-221971 Home & Kitchen furniture null null null null null 1.7234295248170295E9 CUST-16063 AppLogin Mobile S485-7090286144 2024-08-12T02:25:25.51439Z 0 2024-08-12T02:25:25.389Z null null null null null null null null 1.7234295245831337E9 CUST-13727 Browse Product Desktop S806-7767844990 2024-08-12T02:25:25.514655Z 0 2024-08-12T02:25:25.404Z PCA-426149 beauty & health Personal Care Appliances null null null null null 1.7234295256875393E9 CUST-11875 Apply Filter Mobile S128-5985264117 2024-08-12T02:25:26.404585Z 0 2024-08-12T02:25:26.232Z null accessories null null null null null null 1.7234295293363063E9 CUST-17226 Browse Product Desktop S647-5737266877 2024-08-12T02:25:30.014005Z 0 2024-08-12T02:25:29.842Z J-335697 men's clothing Jeans null null null null null 1.723429529922018E9 CUST-08853 Search Desktop S594-7571885355 2024-08-12T02:25:30.780263Z 0 2024-08-12T02:25:30.654Z null Women'S Clothing null null ethnic wear null null null 1.723429530246815E9 CUST-11875 Search Mobile S128-5985264117 2024-08-12T02:25:31.107853Z 0 2024-08-12T02:25:30.92Z null Appliances null null all appliances null null null 1.7234295304006813E9 CUST-16063 Browse Product Mobile S485-7090286144 2024-08-12T02:25:31.108233Z 0 2024-08-12T02:25:31.029Z WW-575375 women's clothing Western Wear null null null null null 1.723429530499204E9 CUST-13727 Browse Product Desktop S806-7767844990 2024-08-12T02:25:31.108347Z 0 2024-08-12T02:25:31.045Z MF-415214 stores Men's Fashion null null null null null 1.7234295336797323E9 CUST-08853 Search Desktop S594-7571885355 2024-08-12T02:25:34.639063Z 0 2024-08-12T02:25:34.483Z null Women'S Clothing null null western wear null null null 1.7234295339805431E9 CUST-15987 Browse Product Desktop S352-3276363757 2024-08-12T02:25:34.857744Z 0 2024-08-12T02:25:34.67Z AE-046994 tv, audio & cameras All Electronics null null null null null 1.7234295341288753E9 CUST-07528 Apply Filter Desktop S308-9517299393 2024-08-12T02:25:34.857929Z 0 2024-08-12T02:25:34.67Z null accessories null null null null null null 1.7234295350993273E9 CUST-11078 Apply Filter Desktop S526-7423099512 2024-08-12T02:25:35.842016Z 0 2024-08-12T02:25:35.608Z null home & kitchen null null null null null null 1.7234295359345906E9 CUST-11875 Search Mobile S128-5985264117 2024-08-12T02:25:36.607621Z 0 2024-08-12T02:25:36.451Z null Tv, Audio & Cameras null null speakers null null null 1.723429537685823E9 CUST-15987 Add to Cart Desktop S352-3276363757 2024-08-12T02:25:38.373376Z 0 2024-08-12T02:25:38.233Z AE-046994 Tv, Audio & Cameras all electronics null null null null null 1.7234295377236638E9 CUST-07528 Browse Product Desktop S308-9517299393 2024-08-12T02:25:38.373563Z 0 2024-08-12T02:25:38.248Z R-430386 bags & luggage Rucksacks null null nu